In [1]:
import pandas as pd, panel as pn
import hvplot.pandas # noqa

In [2]:
@pn.cache()
def get_data():
    df = pd.read_csv('omoku_data.csv', usecols=['Date', 'Power_time', 'Outages'], index_col='Date', parse_dates=True)
    day_of_week = {
    0: 'Monday',
    1: 'Tuesday',
    2: 'Wednesday',
    3: 'Thursday',
    4: 'Friday',
    5: 'Saturday',
    6: 'Sunday'
    }
    df['Day'] = df.index.dayofweek.map(day_of_week)
    return df

In [7]:
data = get_data()
data.head()

Power_time  Outages       Day
Date                                     
2024-03-21        20.5      3.5  Thursday
2024-03-22        19.5      4.5    Friday
2024-03-23        15.5      8.5  Saturday
2024-03-24        21.5      2.5    Sunday
2024-03-25        20.0      4.0    Monday

In [17]:
daily_average = data['Power_time'].mean()
max_power = data['Power_time'].max()
min_power = data['Power_time'].min()

line_plot = data.hvplot.line(y='Power_time')

density_plot = data.hvplot.density('Power_time')

day_order = ['Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Sunday']

weekly_plot = data.groupby('Day', sort=False).mean().reindex(day_order).hvplot.bar(stacked=True, rot=45)


## Dashboard

In [22]:
pn.extension(sizing_mode="stretch_width")

ACCENT = "#4099da"
styles = {
    "box-shadow": "rgba(50, 50, 93, 0.25) 0px 6px 12px -2px, rgba(0, 0, 0, 0.3) 0px 3px 7px -3px",
    "border-radius": "4px",
    "padding": "10px",
}
BRAND_COLOR = ACCENT
BRAND_TEXT_ON_COLOR = "white"
CARD_STYLE = {
  "box-shadow": "rgba(50, 50, 93, 0.25) 0px 6px 12px -2px, rgba(0, 0, 0, 0.3) 0px 3px 7px -3px",
  "padding": "10px",
  "border-radius": "5px"
}
header = pn.Row(
    pn.pane.Markdown(
        "# Omoku power supply report", styles={"color": BRAND_TEXT_ON_COLOR}, margin=(5, 20)
    ),
    styles={"background": BRAND_COLOR},
)
indicators = pn.FlexBox(
    pn.indicators.Number(
        value=daily_average,
        name="Average daily supply (Hrs)",
        format="{value:,.0f}",
        styles=styles
    ),
    pn.indicators.Number(
        value=max_power,
        name="Highest daily supply (Hrs)",
        format="{value:,.1f}",
        styles=styles,
    ),
    pn.indicators.Number(
        value=min_power,
        name="Lowest daily supply (Hrs)",
        format="{value:,.1f}",
        styles=styles,
    ),
)

table = pn.widgets.Tabulator(data.head(10), sizing_mode="stretch_width", name="Table")
tabs = pn.Tabs(
    ('Daily total', line_plot), ('Density plot', density_plot), ('Weekly average', weekly_plot), styles=styles, sizing_mode="stretch_width", height=500, margin=10
)
logo = '<img src="https://panel.pyviz.org/_static/logo_stacked.png" width=180 height=151>'
text = """ This is a [Panel](https://panel.holoviz.org) dashboard that shows the number of hours of power supply in Omoku, Rivers State, Nigeria."""

template = pn.template.FastListTemplate(
    title="Power supply dashboard",
    sidebar=[logo, text],
    main=[pn.Column('# Data Summary', indicators, '# Sample Data', table, '# Plots', tabs, sizing_mode="stretch_both")],
    main_layout=None,
    accent=ACCENT,
)

template.servable();

Launching server at http://localhost:54892
